### Setup and Imports

In [1]:
import sys
from pathlib import Path

sys.path.append(str(Path.cwd().parent))
import config
from src import data_ingestion
from src.symbols import Symbols
from src.portfolio import Portfolio
from src.benchmark import Benchmark

import pandas as pd
import numpy as np
import plotly.graph_objects as go
from plotly.subplots import make_subplots

### Load Transaction Data

In [2]:
# Create a list of all your transaction log files
log_files = [
    config.TRANS_LOG_DIR / "us_mkt_transactions.csv",
    config.TRANS_LOG_DIR / "exus_mkt_transactions.csv",
]

# Load and merge all found logs into a single DataFrame
master_log = data_ingestion.create_master_log(log_files).set_index("Date")
display(master_log)

Type Symbol  Quantity   Price  Amount  Trading Cost  \
Date                                                                            
2023-02-16         Net Deposit    NaN       NaN     NaN  271.57           NaN   
2023-02-17                 buy    VOO  0.218967  372.07  -81.47           NaN   
2023-02-17                 buy   TSLA  0.202666  201.02  -40.74           NaN   
2023-02-17                 buy   PERI  0.407270   33.34  -13.58           NaN   
2023-03-29        Net Dividend    VOO       NaN     NaN    0.24           NaN   
...                        ...    ...       ...     ...     ...           ...   
2025-08-04                 buy    VOO  0.426862  575.08 -245.48           1.0   
2025-08-05        Net Dividend   JPMB       NaN     NaN    0.24           NaN   
2025-08-09  Merger/Acquisition    LUX -2.000000   23.34   46.68           0.0   
2025-08-11        Net Dividend     BX       NaN     NaN    0.24           NaN   
2025-08-11                 buy    VOO  0.078350  586.06  -45.92           1.0   

           Currency                                        Description  \
Date                                                                     
2023-02-16      USD  ID: 37fdafdc-d707-42fa-ba74-98b30cf9ab2a - DT2...   
2023-02-17      USD                                        Trade Entry   
2023-02-17      USD                                        Trade Entry   
2023-02-17      USD                                        Trade Entry   
2023-03-29      USD  Cash DIV @ 1.4874, Pos QTY: 0.218966527, Rec D...   
...             ...                                                ...   
2025-08-04      USD               Purchase of VOO shares on 2025-08-04   
2025-08-05      USD                                     JPMB dividends   
2025-08-09      USD                                 LUX ETF close down   
2025-08-11      USD                                       BX dividends   
2025-08-11      USD                             Purhcase of VOO shares   

             Exchange                 Source  
Date                                          
2023-02-16  US Market            Sarwa Trade  
2023-02-17   NYSEArca            Sarwa Trade  
2023-02-17   NasdaqGS            Sarwa Trade  
2023-02-17   NasdaqGS            Sarwa Trade  
2023-03-29   NYSEArca            Sarwa Trade  
...               ...                    ...  
2025-08-04   NYSEArca  Sarwa Trade - Interim  
2025-08-05   NYSEArca  Sarwa Trade - Interim  
2025-08-09  US Market  Sarwa Trade - Interim  
2025-08-11  US Market  Sarwa Trade - Interim  
2025-08-11  US Market  Sarwa Trade - Interim  

[596 rows x 10 columns]

### Initialize and Assess Symbols

In [3]:
# 1. Initialize the Symbol manager
symbol_manager = Symbols(master_log)

# 2. Assess all symbols (checks cache and yfinance, creates templates for missing symbols)
symbol_manager.assess()

# 3. Display the results for user verification
print("✅ The following symbols were automatically identified:")
found_df = symbol_manager.get_found()
display(found_df)

print("❌ The following symbols were NOT found:")
missing_list = symbol_manager.get_missing()
print(missing_list)

✅ The following symbols were automatically identified:


Name    Type  Exchange  \
Symbol                                                                       
PERI                                 Perion Network Ltd.  equity  NasdaqGS   
TSLA                                         Tesla, Inc.  equity  NasdaqGS   
VOO                                 Vanguard S&P 500 ETF     etf  NYSEArca   
UAE                                 iShares MSCI UAE ETF     etf  NasdaqGM   
XLK               The Technology Select Sector SPDR Fund     etf  NYSEArca   
...                                                  ...     ...       ...   
JPMB    JPMorgan USD Emerging Markets Sovereign Bond ETF     etf  NYSEArca   
SMOT                    VanEck Morningstar SMID Moat ETF     etf   Cboe US   
XLV              The Health Care Select Sector SPDR Fund     etf  NYSEArca   
BX                                       Blackstone Inc.  equity      NYSE   
BRK-B                            Berkshire Hathaway Inc.  equity      NYSE   

       Currency                        Industry                  Sector  \
Symbol                                                                    
PERI        USD  Internet Content & Information  Communication Services   
TSLA        USD              Auto Manufacturers       Consumer Cyclical   
VOO         USD                            None                    None   
UAE         USD                            None                    None   
XLK         USD                            None                    None   
...         ...                             ...                     ...   
JPMB        USD                            None                    None   
SMOT        USD                            None                    None   
XLV         USD                            None                    None   
BX          USD                Asset Management      Financial Services   
BRK-B       USD         Insurance - Diversified      Financial Services   

              Country DataProvider  
Symbol                              
PERI           Israel     yfinance  
TSLA    United States     yfinance  
VOO              None     yfinance  
UAE              None     yfinance  
XLK              None     yfinance  
...               ...          ...  
JPMB             None     yfinance  
SMOT             None     yfinance  
XLV              None     yfinance  
BX      United States     yfinance  
BRK-B   United States     yfinance  

[62 rows x 8 columns]

❌ The following symbols were NOT found:
['ALDAR', 'BURJEEL', 'CHADX15', 'IHC', 'EMAAR', 'MULTIPLY']


### User Correction Step

Reviews the output from the cell above and lists any symbols that were incorrectly identified by the data provider (e.g. `yfinance`).

In [4]:
# User reviews the table above and populates this list
incorrectly_identified_symbols = ["AMR", "ASM"]

# Mark these symbols as user-provided, which also updates the metadata template
symbol_manager.mark_as_manual(incorrectly_identified_symbols)

Updating cache for incorrectly identified symbols: ['AMR', 'ASM']
Caches updated successfully.


### Manual Task

1) Open the file: `data/manual-source/metadata.json`.
2) Fill in the `null` values for all the symbols listed.
3) For each of those same symbols, add a price history CSV file to the `data/manual-source/` directory.

### Reload Metadata and Get Final DataFrame

In [5]:
# Reload the user-edited file from disk
symbol_manager.reload_user_metadata()

# Get the final, combined DataFrame of all symbol metadata
symbol_df = symbol_manager.get_unified_df()

print("--- Final Unified Symbol Metadata ---")
display(symbol_df)

--- Final Unified Symbol Metadata ---


Name    Type  Exchange  \
Symbol                                                                          
PERI                                    Perion Network Ltd.  equity  NasdaqGS   
TSLA                                            Tesla, Inc.  equity  NasdaqGS   
VOO                                    Vanguard S&P 500 ETF     etf  NYSEArca   
UAE                                    iShares MSCI UAE ETF     etf  NasdaqGM   
XLK                  The Technology Select Sector SPDR Fund     etf  NYSEArca   
...                                                     ...     ...       ...   
IHC                      International Holding Company PJSC  equity       ADX   
EMAAR                                 Emaar Properties PJSC  equity       DFM   
MULTIPLY                                Multiply Group PJSC  equity       ADX   
ASM       Al Seer Marine Supplies & Equipment Company P....  equity       ADX   
AMR                 Americana Restaurants International PLC  equity       ADX   

         Currency                        Industry                  Sector  \
Symbol                                                                      
PERI          USD  Internet Content & Information  Communication Services   
TSLA          USD              Auto Manufacturers       Consumer Cyclical   
VOO           USD                            None                    None   
UAE           USD                            None                    None   
XLK           USD                            None                    None   
...           ...                             ...                     ...   
IHC           AED                     Industrials           Conglomerates   
EMAAR         AED       Real Estate - Development             Real Estate   
MULTIPLY      AED                      Financials        Asset Management   
ASM           AED                     Industrials         Marine Shipping   
AMR           AED               Consumer Cyclical             Restaurants   

                       Country DataProvider  
Symbol                                       
PERI                    Israel     yfinance  
TSLA             United States     yfinance  
VOO                       None     yfinance  
UAE                       None     yfinance  
XLK                       None     yfinance  
...                        ...          ...  
IHC       United Arab Emirates       manual  
EMAAR     United Arab Emirates       manual  
MULTIPLY  United Arab Emirates       manual  
ASM       United Arab Emirates       manual  
AMR       United Arab Emirates       manual  

[70 rows x 8 columns]

### Initialize and Run Portfolio Analysis

In [6]:
# Get the project date range
start_date, end_date, date_range, last_market_day = config.project_dates(
    master_log.index
)

# 1. Initialize the Portfolio analysis engine
portfolio = Portfolio(master_log, symbol_manager, date_range, last_market_day)

# 2. Run all calculations (fetching prices, calculating holdings and value)
portfolio.calculate_holdings_and_value()

portfolio_value = portfolio.get_total_value_history()

### Display Portfolio Results

In [7]:
portfolio_value

Date
2023-02-16       0.000000
2023-02-17     137.713026
2023-02-18     137.713026
2023-02-19     137.713026
2023-02-20     137.713026
                 ...     
2025-08-08    3510.601352
2025-08-09    3463.890282
2025-08-10    3464.800117
2025-08-11    3503.781005
2025-08-12    3546.853369
Length: 909, dtype: float64

In [8]:
portfolio.get_current_holdings().round(2).sort_values(
    f"Market Value ({config.BASE_CURRENCY})", ascending=False
)

Shares  Market Value (USD)
VOO         2.06             1215.40
XLK         1.22              328.26
VOOG        0.72              301.95
MOAT        1.40              136.02
MSFT        0.26              135.40
SPY         0.18              114.19
META        0.14              109.48
CHADX15   106.00              104.51
APO         0.53               77.31
XLF         1.31               68.69
JPMB        1.69               66.62
IPO         1.29               65.25
BRK-B       0.12               58.32
BX          0.33               56.61
KKR         0.38               55.69
VXUS        0.72               50.89
INDA        0.88               46.05
NVDA        0.25               45.86
GOF         3.00               45.12
EMAAR      10.00               41.54
LLY         0.06               39.68
BRW         4.71               39.40
BTC-USD     0.00               38.49
XLV         0.29               37.94
AMZN        0.15               33.22
GSBD        2.44               27.73
IJR         0.23               25.99
SMOT        0.72               25.43
TPVG        4.00               25.12
CEFS        1.11               25.12
CLM         2.82               23.01
RYAAY       0.32               20.66
OCSL        1.04               14.15
ARM         0.08               11.51
MULTIPLY   12.00                9.48
USRT        0.17                9.39
IBB         0.05                6.30
BURJEEL    15.00                6.17
AMR         5.00                2.83
ASM         2.00                2.07

In [9]:
portfolio.get_return_summary().round(2)

Income  Realized Gains  Unrealized Gains  Total Return
VOO        8.74           38.58            135.61        182.93
XLK        2.65           53.33             73.41        129.40
VOOG       1.24           15.44             59.22         75.90
META       0.30            0.00             67.14         67.44
SPY        1.71            0.00             36.66         38.37
...         ...             ...               ...           ...
BURJEEL    0.18            0.00             -6.21         -6.03
TQQQ       0.00           -6.11              0.00         -6.11
EL         0.15           -6.54              0.00         -6.39
ROM        0.00           -8.09              0.00         -8.09
TPVG       6.44            0.00            -15.81         -9.37

[70 rows x 4 columns]

In [10]:
total_returns = (
    portfolio.holdings["unrealized_gains"]
    + portfolio.holdings["realized_gains"]
    + portfolio.holdings["income"].cumsum()
)

In [11]:
fig_holdings = go.Figure()

for symbol in total_returns.columns:
    fig_holdings.add_trace(
        go.Scatter(
            x=total_returns.index,
            y=total_returns[symbol],
            mode="lines",
            name=symbol,
            line=dict(width=1),
        )
    )

fig_holdings.update_layout(
    title_text="<b>Individual Holding Performance (Absolute Returns)</b>",
    template="plotly_white",
    xaxis_title="Date",
    yaxis_title=f"Total Returns ({config.BASE_CURRENCY})",
)

fig_holdings.show()

In [12]:
invested_capital = portfolio.holdings['invested_capital'].round(2)
pct_returns = total_returns.div(invested_capital).where(invested_capital > 0, np.nan)

In [13]:
fig_holdings = go.Figure()

for symbol in pct_returns.columns:
    fig_holdings.add_trace(
        go.Scatter(
            x=pct_returns.index,
            y=pct_returns[symbol],
            mode="lines",
            name=symbol,
            line=dict(width=1),
        )
    )

fig_holdings.update_layout(
    title_text="<b>Individual Return on Invested Capital</b>",
    template="plotly_white",
    xaxis_title="Date",
    yaxis_title="Return on Invested Capital (%)",
)

fig_holdings.show()

### Initialize and Run the Benchmark Simulation

In [14]:
# Create an instance of the Benchmark class
benchmark_simulation = Benchmark(master_log, date_range, last_market_day)

# Run benchmark simulation
benchmark_simulation.run_simulation()

### Display Benchmark Result

In [15]:
benchmark_results = benchmark_simulation.get_results()
benchmark_results

Open       Close  Dividends  Market  NetDeposit    Shares  \
Date                                                                          
2023-02-16  375.660004  375.190002        0.0    Open      271.57  0.000000   
2023-02-17  373.179993  374.220001        0.0    Open        0.00  0.725039   
2023-02-18  373.179993  374.220001        0.0  Closed        0.00  0.725039   
2023-02-19  373.179993  374.220001        0.0  Closed        0.00  0.725039   
2023-02-20  373.179993  374.220001        0.0  Closed        0.00  0.725039   
...                ...         ...        ...     ...         ...       ...   
2025-08-08  582.929993  585.739990        0.0    Open        0.00  6.564363   
2025-08-09  582.929993  585.739990        0.0  Closed        0.00  6.564363   
2025-08-10  582.929993  585.739990        0.0  Closed        0.00  6.564363   
2025-08-11  586.030029  584.539978        0.0    Open        0.00  6.564363   
2025-08-12  586.750000  590.780029        0.0    Open        0.00  6.564363   

            DividendCash  TradeCash  Commission  NetDividend  PortfolioValue  \
Date                                                                           
2023-02-16           0.0     271.57         0.0          0.0        0.000000   
2023-02-17           0.0       0.00         1.0          0.0      271.324047   
2023-02-18           0.0       0.00         0.0          0.0      271.324047   
2023-02-19           0.0       0.00         0.0          0.0      271.324047   
2023-02-20           0.0       0.00         0.0          0.0      271.324047   
...                  ...        ...         ...          ...             ...   
2025-08-08           0.0       0.00         0.0          0.0     3845.009943   
2025-08-09           0.0       0.00         0.0          0.0     3845.009943   
2025-08-10           0.0       0.00         0.0          0.0     3845.009943   
2025-08-11           0.0       0.00         0.0          0.0     3837.132627   
2025-08-12           0.0       0.00         0.0          0.0     3878.094589   

             TotalValue TradeTrigger  
Date                                  
2023-02-16     0.000000          Buy  
2023-02-17   271.324047         None  
2023-02-18   271.324047         None  
2023-02-19   271.324047         None  
2023-02-20   271.324047         None  
...                 ...          ...  
2025-08-08  3845.009943         None  
2025-08-09  3845.009943         None  
2025-08-10  3845.009943         None  
2025-08-11  3837.132627         None  
2025-08-12  3878.094589         None  

[909 rows x 13 columns]

Ensure that if base currency is AED or INR and the benchmark prices are in non-base currency, that all benchmark prices are converted to base currency.

### Visualize Portfolio & Benchmark Performance

In [16]:
monthly_deposits = benchmark_results["NetDeposit"].resample("ME").sum()

fig = make_subplots(specs=[[{"secondary_y": True}]])


# Personal Portfolio Value
fig.add_trace(
    go.Scatter(
        x=portfolio_value.index,
        y=portfolio_value,
        mode="lines",
        name="Personal Portfolio",
        line=dict(color="green", width=2),
    ),
    secondary_y=False,
)

# Benchmark Value
fig.add_trace(
    go.Scatter(
        x=benchmark_results.index,
        y=benchmark_results["TotalValue"],
        mode="lines",
        name=f"{config.BENCHMARK_INDEX} Benchmark",
        line=dict(color="red", width=2),
    ),
    secondary_y=False,
)

# Cumulative Net Deposits
fig.add_trace(
    go.Scatter(
        x=benchmark_results.index,
        y=benchmark_results["NetDeposit"].cumsum(),
        mode="lines",
        name="Cumulative Net Deposits",
        line=dict(color="darkgrey", width=1, dash="dash"),
    ),
    secondary_y=False,
)

# Monthly Deposits/Withdrawals (on secondary y-axis)
fig.add_trace(
    go.Bar(
        x=monthly_deposits.index,
        y=monthly_deposits,
        name="Deposits / Withdrawals",
        marker_color="royalblue",
        opacity=0.4,
    ),
    secondary_y=True,
)

fig.update_layout(
    title_text=f"Portfolio Performance vs. {config.BENCHMARK_INDEX} Benchmark",
    template="plotly_white",
    barmode="relative",
    legend=dict(orientation="h", yanchor="bottom", y=1.02, xanchor="right", x=1),
    xaxis_title='Date'
)

fig.update_yaxes(
    title_text=f"<b>Portfolio Value ({config.BASE_CURRENCY})</b>", secondary_y=False
)
fig.update_yaxes(
    title_text="<b>Monthly Cash Flow</b>",
    secondary_y=True,
    showgrid=False,
    layer="below traces",
)

fig.show()

In [17]:
portfolio_income = portfolio.get_monthly_income()
benchmark_income = benchmark_simulation.get_monthly_income()

fig_income_comp = go.Figure()

fig_income_comp.add_trace(
    go.Bar(
        x=portfolio_income.index,
        y=portfolio_income,
        name="Portfolio Income",
        marker_color="mediumseagreen",
    )
)

fig_income_comp.add_trace(
    go.Bar(
        x=benchmark_income.index,
        y=benchmark_income,
        name=f"{config.BENCHMARK_INDEX} Benchmark Income",
        marker_color="grey",
    )
)

fig_income_comp.update_layout(
    title_text="<b>Monthly Income Comparison</b>",
    template="plotly_white",
    barmode="group",
    xaxis_title="Date",
    yaxis_title=f"Net Income ({config.BASE_CURRENCY})",
    legend=dict(orientation="h", yanchor="bottom", y=1.02, xanchor="right", x=1),
)

fig_income_comp.show()